In [ ]:
# [Author]: Jun Yao
# [Date]: 2021-12-03

# [Description] 
# this file prepares the golden labels for topic recognition for TEDLIUM3 dataset,
# it has the following functionalities
# (1) query all links of the 2351 videos from ted.com. The year of some videos 
# are not matched with the year posted, links of these videos have to be fixed manually
# (2) using the links of the videos, send http request to ted.com and get extra metadata,
# such as author, upload date, duration, title, topic labels.
# (3) the final verified golden labels file tedlium3_topic_labels.csv is published
# via Github under MIT license at https://github.com/junyaogz/topic.labels

# input of this script:
# ./stm/*

# output of this script:
# tedlium3_topic_labels.csv

# [Instructions] 
# WARNING! this file runs for more than 36 hours! 
# it needs human intervention to fix some errors since there are some errors in the year 
# of the videos and the search engine of ted.com cannot provide correct links for all videos.
# frequent requests are prohibited by ted.com, so timeout will occur, the last part of this
# code has to be executed repeatedly until all videos are processed succesfully.

In [2]:
import re
import requests
from bs4 import BeautifulSoup
import random
from pathlib import Path
import time

root_path = "/Volumes/SanDisk512/TEDLIUM_release-3/data/stm/"
ted_talk_root = "http://www.ted.com/talks"
ted_web_root = "http://www.ted.com"

def query_video_info(file_name):
    q_sentence = ""

    # find a sentence that has at least 6 words
    # split the sentence, remove date time, <NA> and <UNK>
    with open(root_path+file_name) as file:
        videos = []
        for line in file:
            sleep_time = random.randint(1,4)
            print(f"sleep {sleep_time} seconds to avoid blocking")
            time.sleep(sleep_time)
            tmp = line.split("<NA>")[1].replace("<unk>","").replace("'","").strip()
            #print(tmp)
            q_sentence = tmp
            if len(q_sentence.split(" ")) < 6:
                continue
            
            #remove non-ascii characters
            q_sentence = q_sentence.encode("ascii", "ignore").decode()

            # join words with "+"
            url_q_sentence = "+".join(q_sentence.split(" "))
            #print("Query sentence for {0} is: {1} ".format(file_name, url_q_sentence))

            # add prefix https://www.ted.com/talks?sort=relevance&q=
            request_url = ted_talk_root+"?sort=relevance&q=" + url_q_sentence
            print(request_url)

            # send page request, get the response page
            res1 = ""
            try:
                res1 = requests.get(request_url, timeout=5)
                #print(res1.status_code)
            except:
                print("error: request timeout")
                continue

            res_1_text = ""
            res_1_text = res1.text
            #with open(rootpath + "res1.txt") as file:
            #    res_1_text = file.readlines()

            soup = BeautifulSoup(str(res_1_text))
            #print(soup.prettify())

            candidate_videos = []
            divs = soup.find_all('div', {"class","media__message"})
            for div in divs:
                #print(div.text)   
                link = div.find('a', {"class","ga-link"})
                link_url = link["href"].strip()
                year = div.find('span', {"class","meta__val"})
                tmp = re.findall('[0-9]+', year.text)
                #print(tmp[0])  
                if link_url.startswith("/talks/"):
                    candidate_videos.append([link_url,tmp[0]])

            #print(candidate_videos)

            years_to_match = re.findall('[0-9]+', file_name)
            year_to_match = 0
            if(len(years_to_match)>1):
                year_to_match = years_to_match[1]
            else:
                year_to_match = years_to_match[0]
            #print(year_to_match)
            
            videos = []
            # from the list of search results, match the author and year(maybe +10), select that item
            for v in candidate_videos:
                if abs(int(year_to_match)-int(v[1])) < 3:
                    videos.append(v)

            print(f"found {len(videos)} videos: {videos}")
            #assert len(videos)>=1, "expected matched video num is no less than 1"
            if len(videos)==1:
                break
                
    if len(videos)==0:
        return 0
    
    return videos[0]


# for each stm file, do the following steps
# read stm file

video_uris = []
count = 0
for p in Path(root_path).glob('*.stm'):
    count = count + 1
    fname = p.name
    print(f"------<{count}>----->filepath:{root_path}{fname}")
    videos = query_video_info(fname)
    if videos == 0:
        print("error: no video is found.")
        video_uris.append([fname,"not found"])
    else:
        print(f"selected: {videos[0]}")
        video_uris.append([fname,videos[0]])
    
    sleep_time = random.randint(1,5)
    print(f"sleep {sleep_time} seconds to avoid blocking")
    time.sleep(sleep_time)


------<1>----->filepath:/Volumes/SanDisk512/TEDLIUM_release-3/data/stm/911Mothers_2010W.stm
sleep 2 seconds to avoid blocking
sleep 1 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=the+fact+that+we+have+what+most+people+consider+an+unusual+friendship++and+it+is+and+yet+it+feels+natural+to+us
found 1 videos: [['/talks/aicha_el_wafi_phyllis_rodriguez_the_mothers_who_found_forgiveness_friendship', '2011']]
selected: /talks/aicha_el_wafi_phyllis_rodriguez_the_mothers_who_found_forgiveness_friendship
sleep 5 seconds to avoid blocking
------<2>----->filepath:/Volumes/SanDisk512/TEDLIUM_release-3/data/stm/AalaElKhani_2016X.stm
sleep 3 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=over+one+point+five+billion+people+experience+armed+conflict
found 3 videos: [['/talks/aala_el_khani_what_it_s_like_to_be_a_parent_in_a_war_zone', '2017'], ['/talks/laura_boushnak_the_deadly_legacy_of_cluster_bombs', '2016'], ['/talks/laurel_braitman_depressed_dogs_cats_with

http://www.ted.com/talks?sort=relevance&q=and+the+cat+scan+revealed+no+blood+clots+in+the+lung++but+it+showed
error: request timeout
sleep 3 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=bilateral++visible+palpable+breast+masses+breast+tumors
error: request timeout
sleep 1 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=that+had+metastasized+widely+all+over+the+body
error: request timeout
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=and+the+real+tragedy+was+if+you+look+through+her+records+she+had+been+seen+in+four+or+five+other+health+care+institutions+in+the+preceding+two+years++four+or+five+opportunities
error: request timeout
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=to+see+the+breast+masses+touch+the+breast+mass++intervene+at+a+much+earlier+stage+than+when+we+saw+her
found 1 videos: [['/talks/abraham_verghese_a_doctor_s_touch', '2011']]
selected: /talks/abraham_verghese_a_doct

http://www.ted.com/talks?sort=relevance&q=we+all+took+internships+just+in+case+it+doesn+t+work+out+all+right+but+you+re+going+to+go+in+full+time+once+you+graduate
found 0 videos: []
sleep 1 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=not+exactly+we+ve+all+lined+up+backup+jobs
found 0 videos: []
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=six+months+go+by++it+s+the+day+before+the+company+launches++and+there+is+still+not+a+functioning+website
found 0 videos: []
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=you+guys+realize+the+entire+company+is+a+website+that+s+literally+all+it+is
found 0 videos: []
sleep 3 seconds to avoid blocking
sleep 3 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=i+obviously+declined+to+invest+and+they+ended+up+naming+the+company
found 1 videos: [['/talks/adam_grant_the_surprising_habits_of_original_thinkers', '2016']]
selected: /talks/adam_grant_the_surprisi

found 1 videos: [['/talks/adam_savage_my_love_letter_to_cosplay', '2016']]
selected: /talks/adam_savage_my_love_letter_to_cosplay
sleep 1 seconds to avoid blocking
------<26>----->filepath:/Volumes/SanDisk512/TEDLIUM_release-3/data/stm/AdamSpencer_2013.stm
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=pure+mathematics+and+world+debating+championships++or+as+i+like+to+say+hello+ladies
found 1 videos: [['/talks/adam_spencer_why_i_fell_in_love_with_monster_prime_numbers', '2013']]
selected: /talks/adam_spencer_why_i_fell_in_love_with_monster_prime_numbers
sleep 4 seconds to avoid blocking
------<27>----->filepath:/Volumes/SanDisk512/TEDLIUM_release-3/data/stm/AditiGupta_2015X.stm
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=a+natural+biological+process+that+every+girl+and+woman+goes+through+every+month
found 1 videos: [['/talks/aditi_gupta_a_taboo_free_way_to_talk_about_periods', '2016']]
selected: /talks/aditi_gupta_a_taboo_fre

found 0 videos: []
sleep 1 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=dan+o+brien+jumped+five++eleven+in++ninety+six+in+atlanta++i+mean+if+it+just+gives+you+a+comparison+of+these+are
found 0 videos: []
sleep 4 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=truly+accomplished+athletes+without+qualifying+that+word+athlete+and+so+i+decided+to+give+this+a+shot
found 0 videos: []
sleep 4 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=heart+pounding+i+ran+my+first+race+and+i
found 0 videos: []
sleep 3 seconds to avoid blocking
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=you+ve+got+speed+you+ve+got+natural+speed+but+you
found 0 videos: []
sleep 1 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=don+t+have+any+skill+or+finesse+going+down+that+track+you+were+all+over+the+place
found 0 videos: []
sleep 3 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=we+all+s

...

http://www.ted.com/talks?sort=relevance&q=someone+who+looks+like+me+walks+past+you+in+the+street+do+you+think+they+re+a+mother+a+refugee
found 0 videos: []
sleep 1 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=or+a+victim+of+oppression+or+do+you+think+they+re+a+cardiologist+a+barrister+or+maybe+your+local+politician
found 0 videos: []
sleep 4 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=do+you+look+me+up+and+down+wondering+how+hot+i+must+get+or+if+my+husband+has+forced+me+to+wear+this+outfit
error: request timeout
sleep 4 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=what+if+i+wore+my+scarf+like+this
error: request timeout
sleep 3 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=i+can+walk+down+the+street+in+the+exact+same+outfit+and+what+the+world+expects+of+me+and+the+way+i+m+treated+depends+on+the+arrangement+of+this+piece+of+cloth
found 0 videos: []
sleep 4 seconds to avoid blocking
http://www.ted

found 6 videos: [['/talks/gretchen_carlson_david_brooks_political_common_ground_in_a_polarized_united_states', '2017'], ['/talks/rob_reid_how_synthetic_biology_could_wipe_out_humanity_and_how_we_can_stop_it', '2019'], ['/talks/jon_m_chu_the_pride_and_power_of_representation_in_film', '2019'], ['/talks/tasos_frantzolas_everything_you_hear_on_film_is_a_lie', '2016'], ['/talks/harry_baker_a_love_poem_for_lonely_prime_numbers', '2015'], ['/talks/valarie_kaur_3_lessons_of_revolutionary_love_in_a_time_of_rage', '2018']]
sleep 1 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=they+aren+t+i+mean+it+feels+like+we+need+a+different+kind+of+conversation
found 3 videos: [['/talks/christopher_bell_bring_on_the_female_superheroes', '2016'], ['/talks/ash_beckham_when_to_take_a_stand_and_when_to_let_it_go', '2015'], ['/talks/kelli_jean_drinkwater_enough_with_the_fear_of_fat', '2016']]
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=one+that+s+based+on+i+d

http://www.ted.com/talks?sort=relevance&q=i+woke+up+in+the+middle+of+the+night
found 10 videos: [['/talks/zainab_salbi_women_wartime_and_the_dream_of_peace', '2010'], ['/talks/ronny_edry_israel_and_iran_a_love_story', '2012'], ['/talks/amy_cuddy_your_body_language_may_shape_who_you_are', '2012'], ['/talks/chip_kidd_designing_books_is_no_laughing_matter_ok_it_is', '2012'], ['/talks/ed_gavagan_a_story_about_knots_and_surgeons', '2012'], ['/talks/john_hodgman_aliens_love_where_are_they', '2008'], ['/talks/eve_ensler_what_security_means_to_me', '2008'], ['/talks/misha_glenny_hire_the_hackers', '2011'], ['/talks/jennifer_8_lee_the_hunt_for_general_tso', '2008'], ['/talks/kavita_ramdas_radical_women_embracing_tradition', '2010']]
sleep 2 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=with+the+sound+of+heavy+explosion
found 2 videos: [['/talks/zainab_salbi_women_wartime_and_the_dream_of_peace', '2010'], ['/talks/garik_israelian_how_spectroscopy_could_reveal_alien_life', '

http://www.ted.com/talks?sort=relevance&q=then+let+s+begin++have+you+ever+eaten+a+booger+long+past+your+childhood
found 0 videos: []
sleep 1 seconds to avoid blocking
http://www.ted.com/talks?sort=relevance&q=laughter+it+s+okay+it+s+safe+here
found 10 videos: [['/talks/noel_bairey_merz_the_single_biggest_health_threat_women_face', '2012'], ['/talks/david_kwong_two_nerdy_obsessions_meet_and_it_s_magic', '2014'], ['/talks/larry_smith_why_you_will_fail_to_have_a_great_career', '2012'], ['/talks/elon_musk_the_mind_behind_tesla_spacex_solarcity', '2013'], ['/talks/mark_applebaum_the_mad_scientist_of_music', '2012'], ['/talks/robert_neuwirth_the_power_of_the_informal_economy', '2012'], ['/talks/harry_baker_a_love_poem_for_lonely_prime_numbers', '2015'], ['/talks/stephen_burt_why_people_need_poetry', '2014'], ['/talks/nancy_frates_meet_the_mom_who_started_the_ice_bucket_challenge', '2014'], ['/talks/seth_shostak_et_is_probably_out_there_get_ready', '2012']]
sleep 3 seconds to avoid blocking
h

UnicodeDecodeError: 'utf-8' codec can't decode byte 0xb0 in position 37: invalid start byte

In [3]:
print(f"len of video uris is {len(video_uris)}")
#print(video_uris)

def saveListToFile(list_name, path_to_save):
    fp = open(path_to_save,"w") 
    num = 0
    for line in list_name:
        num = num + 1
        fp.writelines(f"{num}, {line[0]}, {line[1]}\n")    
    fp.close() 

saveListToFile(video_uris, "video_uris.txt")

# remark:
# the above script runs for about 36 hours and outputs file  video_uris.txt
# it contains some missing values (78 out of 2351 videos can not be matched with the videos from ted.com
# using transcript and year when I run it), 
# these videos have to be searched and labelled manually.
# I fixed the missing values manually, added column names, created a new file video_uris_repaired.csv

len of video uris is 2351


In [16]:
import pandas as pd

url_list_file = "video_uris_repaired.csv"

# send page request, get the response page
def extract_video_properties(video_url):
    request_url = ted_web_root + video_url
    print(request_url)

    # send page request, get the response page
    res2 = ""
    try:
        res2 = requests.get(request_url, timeout=5)
        #print(res2.status_code)
    except:
        print("error: request timeout")
        return None
    
    res_2_text = ""
    res_2_text = res2.text
    #with open(rootpath + "res2.txt") as file:
    #    res_2_text = file.readlines()

    soup = BeautifulSoup(str(res_2_text))
    #print(soup.prettify())
    
    #get video intro
    metas = soup.find_all('meta',{"property":"og:video:tag"})
    #choose the first three tags as topics
    topics = ["","",""]
    if len(metas)>0:
        topics[0] = metas[0]["content"].strip()        
    if len(metas)>1:
        topics[1] = metas[1]["content"].strip()
    if len(metas)>2:
        topics[2] = metas[2]["content"].strip()
    #print(topics)
    
    authors = soup.find_all('meta',{"name":"author"})
    author=""
    if len(authors)>0:
        author = authors[0]["content"].strip()
    #print(author)
    
    titles = soup.find_all('meta',{"property":"og:title"})
    title=""
    if len(titles)>0:
        title = titles[0]["content"].strip()
    #print(title)
    
    descs = soup.find_all('meta',{"property":"og:description"})
    desc=""
    if len(descs)>0:
        desc = descs[0]["content"].strip()
    #print(desc)
    
    uploaddates = soup.find_all('meta',{"itemprop":"uploadDate"})
    uploaddate=""
    if len(uploaddates)>0:
        uploaddate = uploaddates[0]["content"].strip()[0:10]
    #print(uploaddate)
    
    durations = soup.find_all('meta',{"itemprop":"duration"})
    duration=""
    if len(durations)>0:
        duration = durations[0]["content"].strip()[2:]
    #print(duration)
    return [title,author,uploaddate, request_url, duration, topics[0],topics[1],topics[2]]

# read all urls from file
v_data = pd.read_csv(url_list_file)
v_data.head()

ID                 FILENAME  \
0   1     911Mothers_2010W.stm   
1   2    AalaElKhani_2016X.stm   
2   3      AaronHuey_2010X.stm   
3   4     AaronKoblin_2011.stm   
4   5   AaronOConnell_2011.stm   

                                                 URI  
0   /talks/aicha_el_wafi_phyllis_rodriguez_the_mo...  
1   /talks/aala_el_khani_what_it_s_like_to_be_a_p...  
2   /talks/aaron_huey_america_s_native_prisoners_...  
3   /talks/aaron_koblin_visualizing_ourselves_wit...  
4   /talks/aaron_o_connell_making_sense_of_a_visi...

In [30]:
df = pd.DataFrame(v_data)
# add new columns to the dataframe
df = df.assign(TITLE="")
df = df.assign(AUTHOR="")
df = df.assign(UPLOAD_DATE="")
df = df.assign(DURATION="")
df = df.assign(TOPIC1="")
df = df.assign(TOPIC2="")
df = df.assign(TOPIC3="")

df_len = len(df)
print(df_len)

df.head()

2351


ID                 FILENAME  \
0   1     911Mothers_2010W.stm   
1   2    AalaElKhani_2016X.stm   
2   3      AaronHuey_2010X.stm   
3   4     AaronKoblin_2011.stm   
4   5   AaronOConnell_2011.stm   

                                                 URI TITLE AUTHOR UPLOAD_DATE  \
0   /talks/aicha_el_wafi_phyllis_rodriguez_the_mo...                            
1   /talks/aala_el_khani_what_it_s_like_to_be_a_p...                            
2   /talks/aaron_huey_america_s_native_prisoners_...                            
3   /talks/aaron_koblin_visualizing_ourselves_wit...                            
4   /talks/aaron_o_connell_making_sense_of_a_visi...                            

  DURATION TOPIC1 TOPIC2 TOPIC3  
0                                
1                                
2                                
3                                
4

In [55]:
# run this part of code repeatedly until all videos are extracted correctly.
for i in range(df_len):
    if df.iloc[i,3] == "": #title is empty
        video_props = extract_video_properties(df.iloc[i,2].strip())
        print(f"video {i+1} properties: {video_props}")
        if video_props:
            df.iloc[i,3] = video_props[0] #title
            df.iloc[i,4] = video_props[1] #author
            df.iloc[i,5] = video_props[2] #upload_date
            df.iloc[i,6] = video_props[4] #duration
            df.iloc[i,7] = video_props[5] #topic1
            df.iloc[i,8] = video_props[6] #topic2
            df.iloc[i,9] = video_props[7] #topic3
        else:
            print("sleep 3 seconds to avoid blocking")
            time.sleep(3)
            continue
        
filtered_df = df[df['TITLE'] == ""]
if len(filtered_df)==0:
    print("successful")
else:
    print(f"{len(filtered_df)} videos failed, please run this part of code again.")

df.head()

#print(df.iloc[1272,2])


successful


ID                 FILENAME  \
0   1     911Mothers_2010W.stm   
1   2    AalaElKhani_2016X.stm   
2   3      AaronHuey_2010X.stm   
3   4     AaronKoblin_2011.stm   
4   5   AaronOConnell_2011.stm   

                                                 URI  \
0   /talks/aicha_el_wafi_phyllis_rodriguez_the_mo...   
1   /talks/aala_el_khani_what_it_s_like_to_be_a_p...   
2   /talks/aaron_huey_america_s_native_prisoners_...   
3   /talks/aaron_koblin_visualizing_ourselves_wit...   
4   /talks/aaron_o_connell_making_sense_of_a_visi...   

                                               TITLE  \
0      The mothers who found forgiveness, friendship   
1        What it's like to be a parent in a war zone   
2                  America's native prisoners of war   
3  Visualizing ourselves ... with crowd-sourced data   
4           Making sense of a visible quantum object   

                              AUTHOR UPLOAD_DATE DURATION         TOPIC1  \
0  Aicha el-Wafi + Phyllis Rodriguez  2011-05-02    9M54S        culture   
1                      Aala El-Khani  2017-02-10   14M16S  communication   
2                         Aaron Huey  2010-11-10   15M27S           TEDx   
3                       Aaron Koblin  2011-05-23   18M18S  collaboration   
4                    Aaron O'Connell  2011-06-02    7M51S     philosophy   

          TOPIC2     TOPIC3  
0  global issues  parenting  
1      community     family  
2        culture    history  
3           data     design  
4        physics    science

In [57]:
# if video 1272 can not be retrieved, fix it manually using the following code
df.iloc[1272,3] = "The unstoppable walk to political reform" #title
df.iloc[1272,4] = "Lawrence Lessig" #author
df.iloc[1272,5] = "2014-04-04" #upload_date
df.iloc[1272,6] = "13M44S" #duration
df.iloc[1272,7] = "corruption" #topic1
df.iloc[1272,8] = "democracy" #topic2
df.iloc[1272,9] = "government" #topic3

df.head()

ID                 FILENAME  \
0   1     911Mothers_2010W.stm   
1   2    AalaElKhani_2016X.stm   
2   3      AaronHuey_2010X.stm   
3   4     AaronKoblin_2011.stm   
4   5   AaronOConnell_2011.stm   

                                                 URI  \
0  /talks/aicha_el_wafi_phyllis_rodriguez_the_mot...   
1  /talks/aala_el_khani_what_it_s_like_to_be_a_pa...   
2  /talks/aaron_huey_america_s_native_prisoners_o...   
3  /talks/aaron_koblin_visualizing_ourselves_with...   
4  /talks/aaron_o_connell_making_sense_of_a_visib...   

                                               TITLE  \
0      The mothers who found forgiveness, friendship   
1        What it's like to be a parent in a war zone   
2                  America's native prisoners of war   
3  Visualizing ourselves ... with crowd-sourced data   
4           Making sense of a visible quantum object   

                              AUTHOR UPLOAD_DATE DURATION         TOPIC1  \
0  Aicha el-Wafi + Phyllis Rodriguez  2011-05-02    9M54S        culture   
1                      Aala El-Khani  2017-02-10   14M16S  communication   
2                         Aaron Huey  2010-11-10   15M27S           TEDx   
3                       Aaron Koblin  2011-05-23   18M18S  collaboration   
4                    Aaron O'Connell  2011-06-02    7M51S     philosophy   

          TOPIC2     TOPIC3  
0  global issues  parenting  
1      community     family  
2        culture    history  
3           data     design  
4        physics    science

In [62]:
# save the pd to csv
for i in range(df_len):
    df.iloc[i,1] = df.iloc[i,1].strip() #remove spaces
    df.iloc[i,2] = df.iloc[i,2].strip() #remove spaces
    
df.to_csv('tedlium3_topic_labels.csv',index=False)